In [1]:
import pandas as pd
#import chart_studio.plotly as py
#import plotly.offline as po
#import plotly.express as px
#import plotly.graph_objs as pg
import matplotlib.pyplot as plt
#import plotly.graph_objects as go
import folium
from folium import plugins
from folium import features
from folium.plugins import GroupedLayerControl, MarkerCluster, TagFilterButton
import geopandas as gpd
%matplotlib inline

In [2]:
from IPython.core.display import display, HTML
display(HTML("<style>.container {width:75% !important; }</style>"))

C:\Users\marsavin\AppData\Local\Temp\ipykernel_19184\3902864254.py:1: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


In [3]:
counties = gpd.read_file("C:\\Users\marsavin\Desktop\FortCollins_AQmonitoring\Shapefiles\Colorado_County_Boundaries.shp")
FoCo_city_limit = gpd.read_file("C:\\Users\marsavin\Desktop\FortCollins_AQmonitoring\Shapefiles\City_Limits.shp")

geojson_counties = counties.to_crs(epsg='4326').__geo_interface__
geojson_FoCo_city_limit = FoCo_city_limit.to_crs(epsg='4326').__geo_interface__

In [5]:
map =  folium.Map(location=[40.5, -105], zoom_start=9)

aq_sites = pd.read_excel('C:\\Users\\marsavin\\Desktop\\FortCollins_AQmonitoring\\SiteInfo_v3.xlsx')
folium.GeoJson(geojson_counties, name="Colorado County Borders", style_function=lambda feature: {'color': 'blue', 'weight': 2, 'fillOpacity': 0.00}).add_to(map)
folium.GeoJson(FoCo_city_limit, name="Fort Collins City Limit", style_function=lambda feature: {'color': 'blue','weight': 2,'fillOpacity': 0.1}).add_to(map)

O3 = folium.FeatureGroup(name='Ozone').add_to(map)
CO = folium.FeatureGroup(name='Carbon Monoxide').add_to(map)
NH3 = folium.FeatureGroup(name='Gas-phase Ammonia (NH3)').add_to(map)
D = folium.FeatureGroup(name='Wet and/or Dry Deposition').add_to(map)
PM = folium.FeatureGroup(name='Particulate Matter (PM)').add_to(map)
VOC = folium.FeatureGroup(name='Volitale Organic Compounds (VOCs)').add_to(map)
NOx = folium.FeatureGroup(name='Nitrogen Oxides (NOx)').add_to(map)

for index, row in aq_sites.iterrows():
    #define single-monitor site popup text
    AQS_noLink = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b><br>AQS ID: {row['AQS_ID']}\
             <br><br><i>{row['Info']}</i>\
             <br>-Agency/Program: {row['Agency']}\
             <br>-Years active: {row['Years_Active']}\
             <br>-Sampling resolution: {row['Sampling_Resolution']}\
             <br>-Method:</i> {row['Method']}"
    AQS_Link = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b><br>AQS ID: {row['AQS_ID']}\
               <br><br><i>{row['Info']}</i>\
               <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a></i>\
               <br>-Agency/Program: {row['Agency']}\
               <br>-Years active: {row['Years_Active']}\
               <br>-Sampling resolution: {row['Sampling_Resolution']}\
               <br>-Method: {row['Method']}"
    Special_Link = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b>\
            <br><i>{row['Info']}</i>\
            <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a>\
            <br><br>-Agency/Program: {row['Agency']}\
            <br>-Years active: {row['Years_Active']}\
            <br>-Sampling resolution: {row['Sampling_Resolution']}\
            <br>-Method: {row['Method']}"
    
    #shared multi-site popups: 
    Special_2Links = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b>\
                       <br><br><i>{row['Info']}</i>\
                       <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a></i>\
                       <br>-Agency/Program: {row['Agency']}\
                       <br>-Years active: {row['Years_Active']}\
                       <br>-Sampling resolution: {row['Sampling_Resolution']}\
                       <br>-Method: {row['Method']}\
                       <br><br><i>{row['Info2']}</i>\
                       <br><a href={row['Link2']} target='_blank'>{row['Link_Info2']}</a></i>\
                       <br>-Agency/Program: {row['Agency2']}\
                       <br>-Years active: {row['Years_Active2']}\
                       <br>-Sampling resolution: {row['Sampling_Resolution2']}\
                       <br>-Method: {row['Method2']}"  
    
    Special_3Links = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b>\
                       <br><br><i>{row['Info']}</i>\
                       <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a></i>\
                       <br>-Agency/Program: {row['Agency']}\
                       <br>-Years active: {row['Years_Active']}\
                       <br>-Sampling resolution: {row['Sampling_Resolution']}\
                       <br>-Method: {row['Method']}\
                       <br><br><i>{row['Info2']}</i>\
                       <br><a href={row['Link2']} target='_blank'>{row['Link_Info2']}</a></i>\
                       <br>-Agency/Program: {row['Agency2']}\
                       <br>-Years active: {row['Years_Active2']}\
                       <br>-Sampling resolution: {row['Sampling_Resolution2']}\
                       <br>-Method: {row['Method2']}\
                       <br><br><i>{row['Info3']}</i>\
                       <br><a href={row['Link3']} target='_blank'>{row['Link_Info3']}</a></i>\
                       <br>-Agency/Program: {row['Agency3']}\
                       <br>-Years active: {row['Years_Active3']}\
                       <br>-Sampling resolution: {row['Sampling_Resolution3']}\
                       <br>-Method: {row['Method3']}"  
    
    #add markers, define new popup text for multi-monitor markers
    if row['Site'] == 'Fort Collins West':
        if 'Ozone-Active' in row['Species']:
            FortCollinsW = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b><br>AQS ID: {row['AQS_ID']}\
                         <br><br><i>{row['Info']}</i>\
                         <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a>\
                         <br>-Agency/Program: {row['Agency']}\
                         <br>-Years active: {row['Years_Active']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution']}\
                         <br>-Method: {row['Method']}\
                         <br><br><i>{row['Info2']}</i>"
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FortCollinsW, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='blue', icon='ellipsis', prefix='fa')).add_to(O3)               
        if 'VOCs-Planned' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FortCollinsW, max_width=400), tags=['Planned'], 
                          icon=folium.Icon(color='orange', icon='ellipsis', prefix='fa')).add_to(VOC)       
        if 'NOx-Planned' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FortCollinsW, max_width=400), tags=['Planned'], 
                          icon=folium.Icon(color='purple', icon='ellipsis', prefix='fa')).add_to(NOx)
        if 'PM-Planned' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FortCollinsW, max_width=400), tags=['Planned'], 
                          icon=folium.Icon(color='gray', icon='ellipsis', prefix='fa')).add_to(PM)
        
    if row['Site'] == 'CSU - S. Mason':
        if 'Ozone-Active' in row['Species']:
            CSUSMason = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b><br>AQS ID: {row['AQS_ID']}\
                        <br><br><i>{row['Info']}</i>\
                        <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a>\
                        <br>-Agency/Program: {row['Agency']}\
                        <br>-Years active: {row['Years_Active']}\
                        <br>-Sampling resolution: {row['Sampling_Resolution']}\
                        <br>-Method:{row['Method']}\
                        <br><br><i>{row['Info2']}</i>\
                        <br>-Agency/Program: {row['Agency2']}\
                        <br>-Years active: {row['Years_Active2']}\
                        <br>-Sampling resolution: {row['Sampling_Resolution2']}\
                        <br>-Method: {row['Method2']}"
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(CSUSMason, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='blue', icon='ellipsis', prefix='fa')).add_to(O3) 
        if 'CO-Active' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(CSUSMason, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='red', icon='ellipsis', prefix='fa')).add_to(CO) 
     
    if row['Site'] == 'RMNP Longs Peak':
        if 'Ozone-Active' in row['Species']:
            LongsPeak = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b><br>AQS ID: {row['AQS_ID']}\
                         <br><br><i>{row['Info']}</i>\
                         <br>-Agency/Program: {row['Agency']}\
                         <br>-Years active: {row['Years_Active']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution']}\
                         <br>-Method: {row['Method']}\
                         <br><br><i>{row['Info2']}</i>\
                         <br><a href={row['Link']} target='_blank'>{row['Link_Info']}</a></i>\
                         <br>-Agency/Program: {row['Agency2']}\
                         <br>-Years active: {row['Years_Active2']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution2']}\
                         <br>-Method: {row['Method2']}\
                         <br><br><i>{row['Info3']}</i>\
                         <br>Site information:<a href={row['Link2']} target='_blank'> {row['Link_Info2']};  </a><a href={row['Link3']} target='_blank'>{row['Link_Info3']} </a>\
                         <br>-Agency/Program: {row['Agency3']}\
                         <br>-Years active: {row['Years_Active3']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution3']}\
                         <br>-Method: {row['Method3']}\
                         <br><br><i>{row['Info4']}</i>\
                         <br><a href={row['Link4']} target='_blank'>{row['Link_Info4']}</a>\
                         <br>-Agency/Program: {row['Agency4']}\
                         <br>-Years active: {int(row['Years_Active4'])}\
                         <br>-Sampling resolution: {row['Sampling_Resolution4']}\
                         <br>-Method: {row['Method4']}\
                         <br><br><i>{row['Info5']}</i>\
                         <br><a href={row['Link5']} target='_blank'>{row['Link_Info5']}</a>\
                         <br>-Agency/Program: {row['Agency5']}\
                         <br>-Years active: {row['Years_Active5']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution5']}\
                         <br>-Method: {row['Method5']}\
                         <br><br><img src='{row['Image']}' alt='Image' style='width: 400px; height: auto;'>"                
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(LongsPeak, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='blue', icon='ellipsis', prefix='fa')).add_to(O3)               
        if 'PM-Active' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(LongsPeak, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='gray', icon='ellipsis', prefix='fa')).add_to(PM)       
        if 'D-Active' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(LongsPeak, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='darkblue', icon='ellipsis', prefix='fa')).add_to(D)
        if 'VOCs-Inactive' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(LongsPeak, max_width=400), tags=['Inactive'], 
                          icon=folium.Icon(color='orange', icon='ellipsis', prefix='fa')).add_to(VOC)
        if 'NH3-Inactive' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(LongsPeak, max_width=400), tags=['Inactive'], 
                          icon=folium.Icon(color='green', icon='ellipsis', prefix='fa')).add_to(NH3)
            
    if row['Site'] == 'Bethke Elementary School':
        if 'VOCs-Inactive' in row['Species']:             
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_2Links, max_width=400), tags=['Inactive'], 
                          icon=folium.Icon(color='orange', icon='ellipsis', prefix='fa')).add_to(VOC)               
        if 'NH3-Inactive' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_2Links, max_width=400), tags=['Inactive'], 
                          icon=folium.Icon(color='green', icon='ellipsis', prefix='fa')).add_to(NH3) 
            
    if row['Site'] == 'NADP CO81':
        if 'NH3-Active' in row['Species']:              
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_2Links, max_width=300), tags=['Active'], 
                          icon=folium.Icon(color='green', icon='ellipsis', prefix='fa')).add_to(NH3)               
        if 'D-Active' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_2Links, max_width=300), tags=['Active'], 
                          icon=folium.Icon(color='darkblue', icon='ellipsis', prefix='fa')).add_to(D)
            
    if row['Site'] == 'NADP CO13':
        if 'NH3-Inactive' in row['Species']:              
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_3Links, max_width=300), tags=['Inactive'], 
                          icon=folium.Icon(color='green', icon='ellipsis', prefix='fa')).add_to(NH3)               
        if 'D-Inactive' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_3Links, max_width=300), tags=['Inactive'], 
                          icon=folium.Icon(color='darkblue', icon='ellipsis', prefix='fa')).add_to(D) 
            
    if row['Site'] == 'Fossil Creek Resevoir':
        if 'Ozone-Planned' in row['Species']:
            FossilCreek = f"<div style='font-family: Arial; font-size: 14px'><b> {row['Site']}</b>\
                         <br><br><i>{row['Info']}</i>\
                         <br>-Agency/Program: {row['Agency']}\
                         <br>-Years active: {row['Years_Active']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution']}\
                         <br>-Method: {row['Method']}\
                         <br><br><i>{row['Info2']}</i>\
                         <br><a href={row['Link2']} target='_blank'>{row['Link_Info2']}</a></i>\
                         <br>-Agency/Program: {row['Agency2']}\
                         <br>-Years active: {row['Years_Active2']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution2']}\
                         <br>-Method: {row['Method2']}\
                         <br><br><i>{row['Info3']}</i>\
                         <br><a href={row['Link3']} target='_blank'> {row['Link_Info3']}</a>\
                         <br>-Agency/Program: {row['Agency3']}\
                         <br>-Years active: {row['Years_Active3']}\
                         <br>-Sampling resolution: {row['Sampling_Resolution3']}\
                         <br>-Method: {row['Method3']}"                
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FossilCreek, max_width=400), tags=['Planned'], 
                          icon=folium.Icon(color='blue', icon='ellipsis', prefix='fa')).add_to(O3)               
        if 'VOCs-Inactive' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FossilCreek, max_width=400), tags=['Inactive'], 
                          icon=folium.Icon(color='orange', icon='ellipsis', prefix='fa')).add_to(PM)
        if 'PM-Active' in row['Species']:
            folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(FossilCreek, max_width=400), tags=['Active'], 
                          icon=folium.Icon(color='gray', icon='ellipsis', prefix='fa')).add_to(PM)    
            
    if row['Site'] == 'Rist Canyon' or row['Site'] == 'Deadman':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(AQS_noLink, max_width=400), tags=['Inactive'], 
                      icon=folium.Icon(color='blue', icon='square', prefix='fa')).add_to(O3)
        
    if row['Site'] == 'RMNP Trail Ridge Road':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Inactive'], 
                      icon=folium.Icon(color='blue', icon='square', prefix='fa')).add_to(O3)
        
    if row['Site'] == 'CSU - Powerhouse':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=300), tags=['Inactive'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM)
        
    if row['Site'] == 'Soapstone Prairie - PM':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Active'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM)
        
    if row['Site'] == 'Soapstone Prairie - VOCs':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Inactive'], 
                      icon=folium.Icon(color='orange', icon='square', prefix='fa')).add_to(VOC)
        
    if row['Site'] == 'S. College':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(AQS_noLink, max_width=300), tags=['Inactive'], 
                      icon=folium.Icon(color='red', icon='square', prefix='fa')).add_to(CO) 
        
    if row['Site'] == 'FOCO1' or row['Site'] == 'CSU - Edison':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(AQS_Link, max_width=300), tags=['Active'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM)
        
    if row['Site'] == 'Laporte' or row['Site'] == 'Oak St.':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(AQS_noLink, max_width=300), tags=['Inactive'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM) 

    if row['Site'] == 'RMNP Headquarters':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(AQS_Link, max_width=300), tags=['Inactive'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM)
        
    if row['Site'] == 'Museum of Discovery':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Active'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM) 
        
    if row['Site'] == 'Gardens on Spring Creek':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Active'], 
                      icon=folium.Icon(color='blue', icon='square', prefix='fa')).add_to(O3)
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Active'], 
                      icon=folium.Icon(color='gray', icon='square', prefix='fa')).add_to(PM) 
        
    if row['Species'] == 'VOCs-Inactive':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=400), tags=['Inactive'], 
                      icon=folium.Icon(color='orange', icon='square', prefix='fa')).add_to(VOC)
        
    if row['Species'] == 'NH3-Active':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=300), tags=['Active'], 
                      icon=folium.Icon(color='green', icon='square', prefix='fa')).add_to(NH3)
        
    if row['Species'] == 'NH3-Inactive':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=300), tags=['Inactive'], 
                      icon=folium.Icon(color='green', icon='square', prefix='fa')).add_to(NH3)
        
    if row['Species'] == 'D-Active':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=300), tags=['Active'], 
                      icon=folium.Icon(color='darkblue', icon='square', prefix='fa')).add_to(D)
        
    if row['Species'] == 'D-Inactive':
        folium.Marker([row['Latitude'], row['Longitude']], popup=folium.Popup(Special_Link, max_width=300), tags=['Inactive'], 
                      icon=folium.Icon(color='darkblue', icon='square', prefix='fa')).add_to(D)
        
tag_filter = TagFilterButton(['Active','Inactive','Planned'], clear_text='Status').add_to(map)
folium.LayerControl(collapsed=False, hideSingleBase=True).add_to(map)

GroupedLayerControl(
        groups={
      'Species Measured:': [O3, CO, PM, VOC, NOx, NH3, D]},
    exclusive_groups=False,
    collapsed=False,
).add_to(map)

map.save("C:\\Users\\marsavin\\Desktop\\FortCollins_AQmonitoring\\FortCollins_AQ_map_v3.html")
map